In [4]:
from google.colab import userdata, files
wnbkey = userdata.get('WNBKEY')
hftoken = userdata.get('HFTOKEN')

In [5]:
from huggingface_hub import login
login(hftoken)

In [6]:
import wandb
wandb.login(key=wnbkey)

wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: arashghsz (arashghsz-tampere-university) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


True

In [7]:
files.upload()

Saving ipxact_component_dataset.json to ipxact_component_dataset.json


{'ipxact_component_dataset.json': b'[\n  {\n    "instruction": "Create an IP-XACT component for wishbone with Specification of wishbone bus is available at: http://cdn.opencores.org/downloads/wbspec_b4.pdf\\n\\nClock and reset signals are not specifically master-to-slave signals nor vice versa, but instead they come from a third party that assumes neither mode.\\n\\nNotice that while multiple slaves and masters are supported, broadcasts are not. Thus an arbiter will be required, unless it is a single master to single slave connection..",\n    "response": "<?xml version=\\"1.0\\" encoding=\\"UTF-8\\"?>\\n<ipxact:busDefinition xmlns:xsi=\\"http://www.w3.org/2001/XMLSchema-instance\\" xmlns:ipxact=\\"http://www.accellera.org/XMLSchema/IPXACT/1685-2014\\" xmlns:kactus2=\\"http://kactus2.cs.tut.fi\\" xsi:schemaLocation=\\"http://www.accellera.org/XMLSchema/IPXACT/1685-2014/ http://www.accellera.org/XMLSchema/IPXACT/1685-2014/index.xsd\\">\\n\\t<ipxact:vendor>opencores.org</ipxact:vendor>\\n

In [8]:
!pip install -q -U accelerate peft bitsandbytes transformers trl

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.8/410.8 kB 14.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.1/76.1 MB 11.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.2/10.2 MB 123.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 335.7/335.7 kB 25.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 487.4/487.4 kB 37.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 59.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 36.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 41.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 14.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [9]:
!pip install datasets

In [10]:
import pandas as pd
import torch
from transformers import (
    AutoModelForCausalLM,
    CodeLlamaTokenizer,
    default_data_collator,
    Trainer,
    TrainingArguments,
    TrainerCallback,
    BitsAndBytesConfig,
    AutoTokenizer,
)
from contextlib import nullcontext
from tqdm import tqdm
import json
import copy
from datasets import Dataset
from peft import LoraConfig, PeftConfig
from transformers import default_data_collator, Trainer

In [11]:
json_file = pd.read_json("ipxact_component_dataset.json")
json_file
dataset = Dataset.from_pandas(pd.DataFrame(json_file))
dataset[0]

{'instruction': 'Create an IP-XACT component for wishbone with Specification of wishbone bus is available at: http://cdn.opencores.org/downloads/wbspec_b4.pdf\n\nClock and reset signals are not specifically master-to-slave signals nor vice versa, but instead they come from a third party that assumes neither mode.\n\nNotice that while multiple slaves and masters are supported, broadcasts are not. Thus an arbiter will be required, unless it is a single master to single slave connection..',
 'response': '<?xml version="1.0" encoding="UTF-8"?>\n<ipxact:busDefinition xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xmlns:ipxact="http://www.accellera.org/XMLSchema/IPXACT/1685-2014" xmlns:kactus2="http://kactus2.cs.tut.fi" xsi:schemaLocation="http://www.accellera.org/XMLSchema/IPXACT/1685-2014/ http://www.accellera.org/XMLSchema/IPXACT/1685-2014/index.xsd">\n\t<ipxact:vendor>opencores.org</ipxact:vendor>\n\t<ipxact:library>interface</ipxact:library>\n\t<ipxact:name>wishbone</ipxact:name>

In [12]:
model_name = "meta-llama/CodeLlama-7b-Instruct-hf"

# compute_dtype = getattr(torch, "float16")

# bnb_config = BitsAndBytesConfig(
#     load_in_4bit=True,
#     bnb_4bit_use_double_quant=True,
#     bnb_4bit_quant_type="nf4",
#     bnb_4bit_compute_dtyp=torch.bfloat16
# )

model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map="auto",
    trust_remote_code=True,
    load_in_8bit=True
#     quantization_config=bnb_config,
)

model.config.use_cache = False

tokenizer = AutoTokenizer.from_pretrained(model_name,
                                          trust_remote_code=True,
                                         )
tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right"

config.json:   0%|          | 0.00/646 [00:00<?, ?B/s]

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


model.safetensors.index.json:   0%|          | 0.00/25.1k [00:00<?, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/9.98G [00:00<?, ?B/s]

...

generation_config.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/1.59k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.84M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/411 [00:00<?, ?B/s]

In [13]:
def get_preprocessed_cmg_history(dataset, tokenizer, split):

    def apply_prompt_template(sample):
        return {
            "prompt": sample["instruction"],
            "message": sample["response"],
        }

    dataset = dataset.map(apply_prompt_template, remove_columns=list(dataset.features))

    # mx = 0

    def tokenize_add_label(sample):
        prompt = tokenizer.encode(tokenizer.bos_token + sample["prompt"], add_special_tokens=False, max_length=200, truncation=True)
        message = tokenizer.encode(sample["message"] +  tokenizer.eos_token, max_length=400, truncation=True, add_special_tokens=False)

        if len(prompt) == 0:
            prompt = [tokenizer.pad_token_id]  # Add a pad token to prevent empty tensors
        if len(message) == 0:
            message = [tokenizer.pad_token_id]

        max_length = 601 - len(prompt) - len(message)
        # mx = max(mx, len(prompt) + len(message))
        if max_length < 0:
            print("OK")

        pad = tokenizer.encode(tokenizer.eos_token, add_special_tokens=False, max_length=max_length, padding='max_length', truncation=True)

        sample = {
            "input_ids": prompt + message + pad,
            "attention_mask" : [1] * (len(prompt) + len(message) + len(pad)),
            "labels": [-100] * len(prompt) + message + [-100] * len(pad),
            }

        return sample

    dataset = dataset.map(tokenize_add_label, remove_columns=list(dataset.features))

    # print(mx)
    return dataset

In [14]:
train_dataset = get_preprocessed_cmg_history(dataset, tokenizer, 'train')

Map:   0%|          | 0/286 [00:00<?, ? examples/s]

Map:   0%|          | 0/286 [00:00<?, ? examples/s]

In [15]:
from peft import prepare_model_for_kbit_training

In [16]:
def create_peft_config(model):
    from peft import (
        get_peft_model,
        LoraConfig,
        TaskType,
        prepare_model_for_kbit_training,
    )

    peft_config = LoraConfig(
        task_type=TaskType.CAUSAL_LM,
        inference_mode=False,
        r=4,
        lora_alpha=64,
        lora_dropout=0.1,
        target_modules = ["q_proj", "v_proj"]
    )

    # prepare int-8 model for training
    model = prepare_model_for_kbit_training(model)
    model = get_peft_model(model, peft_config)
    model.print_trainable_parameters()
    return model, peft_config


model, lora_config = create_peft_config(model)

training_arguments = TrainingArguments(
    output_dir="logs",
    num_train_epochs=2,
    per_device_train_batch_size=4,
    gradient_accumulation_steps=2, # 4
    optim="paged_adamw_32bit",
    save_steps=0,
    logging_steps=10,
    learning_rate=2e-4,
    fp16=True,
    bf16=False,
    group_by_length=True,
    logging_strategy="steps",
    save_strategy="no",
    gradient_checkpointing=False,
)

trainer = Trainer(
    model=model,
    args=training_arguments,
    train_dataset=train_dataset,
    data_collator=default_data_collator,
)


trainable params: 2,097,152 || all params: 6,740,643,840 || trainable%: 0.0311


No label_names provided for model class `PeftModelForCausalLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


In [17]:
import torch; print(torch.__version__)

2.6.0+cu124


In [18]:
trainer.train()

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.


/usr/local/lib/python3.11/dist-packages/torch/_dynamo/eval_frame.py:745: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.5 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)
/usr/local/lib/python3.11/dist-packages/bitsandbytes/autograd/_functions.py:315: UserWarning: MatMul8bitLt: inputs will be cast from torch.float32 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")


TrainOutput(global_step=72, training_loss=0.1885178881800837, metrics={'train_runtime': 1666.9487, 'train_samples_per_second': 0.343, 'train_steps_per_second': 0.043, 'total_flos': 1.3632979206832128e+16, 'train_loss': 0.1885178881800837, 'epoch': 2.0})

In [ ]:
model.push_to_hub("nutukoira/ipxact.3.0")
tokenizer.push_to_hub("nutukoira/ipxact.3.0")

adapter_model.safetensors:   0%|          | 0.00/8.41M [00:00<?, ?B/s]

README.md:   0%|          | 0.00/5.17k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/nutukoira/ipxact.3.0/commit/cba5310ce3ab763221d2ff78ca442ad2d04fd614', commit_message='Upload tokenizer', commit_description='', oid='cba5310ce3ab763221d2ff78ca442ad2d04fd614', pr_url=None, repo_url=RepoUrl('https://huggingface.co/nutukoira/ipxact.3.0', endpoint='https://huggingface.co', repo_type='model', repo_id='nutukoira/ipxact.3.0'), pr_revision=None, pr_num=None)

In [36]:
import ipywidgets as widgets
from IPython.display import display

# Create a larger input field and button
text_input = widgets.Text(
    placeholder="Enter your query to generate IP-XACP component here...",
    layout=widgets.Layout(width="800px", height="40px")  # Adjust width and height
)
submit_button = widgets.Button(
    description="Submit",
    layout=widgets.Layout(width="150px", height="40px")  # Make button bigger
)

# Define the button click event
def on_submit(b):
    model.eval()
    eval_prompt = text_input.value
    #Generate an IP‑XACT component for a UART interface including registers for baud rate, control, status, and data.
    model_input = tokenizer(eval_prompt, return_tensors="pt").to("cuda")

    with torch.no_grad():
        output = tokenizer.decode(model.generate(**model_input, max_new_tokens = 2048, pad_token_id=tokenizer.eos_token_id)[0], skip_special_tokens=True)

    print(output)
    print(f"Submitted: {text_input.value}")

submit_button.on_click(on_submit)

# Display widgets
display(text_input, submit_button)

Text(value='', layout=Layout(height='40px', width='800px'), placeholder='Enter your query to generate IP-XACP …

Button(description='Submit', layout=Layout(height='40px', width='150px'), style=ButtonStyle())

Generate an IP‑XACT component for a UART interface including registers for baud rate, control, status, and data. <?xml version="1.0" encoding="UTF-8"?>
<ipxact:component xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xmlns:ipxact="http://www.accellera.org/XMLSchema/IPXACT/1685-2014" xmlns:kactus2="http://kactus2.cs.tut.fi" xsi:schemaLocation="http://www.accellera.org/XMLSchema/IPXACT/1685-2014 http://www.accellera.org/XMLSchema/IPXACT/1685-2014/index.xsd">
	<ipxact:vendor>pulp-platform.org</ipxact:vendor>
	<ipxact:library>interface</ipxact:library>
	<ipxact:name>uart</ipxact:name>
	<ipxact:version>1.0</ipxact:version>
	<ipxact:busInterfaces>
		<ipxact:busInterface>
			<ipxact:name>rx</ipxact:name>
			<ipxact:busType vendor="pulp-platform.org" library="interface" name="uart_rx" version="1.0"/>
			<ipxact:abstractionTypes>
				<ipxact:abstractionType>
					<ipxact:abstractionRef vendor="pulp-platform.org" library="interface" name="uart_rx.absDef" version="1.0"/>
					<ipxact:portM

In [56]:
!pip install --upgrade openai

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 606.1/606.1 kB 16.6 MB/s eta 0:00:00
  Attempting uninstall: openai
    Found existing installation: openai 1.66.5
    Uninstalling openai-1.66.5:
      Successfully uninstalled openai-1.66.5


In [80]:
from google.colab import userdata
from openai import OpenAI
import os

# Initialize the OpenAI client with your API key
client = OpenAI(api_key=userdata.get("OPENAI_API_KEY"))

# Debugging: Print the API key status (masking for security)
if client.api_key:
    print("API Key successfully retrieved.")
else:
    print("API Key not found. Please ensure it's set in Colab secrets under the name 'OPENAI_API_KEY'.")

def assess_and_save_xml(xml_data, component_name):
    if not client.api_key:
        print("OpenAI API key is missing. Please check Colab secrets.")
        return

    prompt = f"""
    Assess the following XML component and provide a final assessment:

    XML Component:
    {xml_data}

    🔍 Final Assessment:
    1. XML Well-Formed: ✅ Pass or ❌ Fail
    2. Schema Compliance: ✅ Pass or ❌ Fail
    3. Bus Interfaces Valid: ✅ Pass or ❌ Fail
    4. Port Mappings Correct: ✅ Pass or ❌ Fail
    5. Component References Exist?: ✅ Pass or ❌ Fail
    6. UUIDs Unique?: ✅ Pass or ❌ Fail
    """

    try:
        response = client.chat.completions.create(
            model="gpt-3.5-turbo",
            messages=[
                {"role": "system", "content": "You are a helpful assistant."},
                {"role": "user", "content": prompt}
            ],
            max_tokens=150,
            temperature=0.5,
        )

        assessment = response.choices[0].message.content.strip()

        # Save XML component to a file
        xml_file_path = f"/content/{component_name}.xml"
        with open(xml_file_path, "w") as f:
            f.write(xml_data)
        print(f"XML Component saved as {xml_file_path}")

        # Save assessment to a file
        assessment_file_path = f"/content/{component_name}_assessment.txt"
        with open(assessment_file_path, "w") as f:
            f.write("🔍 Final Assessment\n\n")
            f.write(assessment)
        print(f"Assessment saved as {assessment_file_path}")

    except Exception as e:
        print(f"Error with OpenAI API: {e}")

# Example Usage
xml_data = """<ipxact:component xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xmlns:ipxact="http://www.accellera.org/XMLSchema/IPXACT/1685-2014" xmlns:kactus2="http://kactus2.cs.tut.fi" xsi:schemaLocation="http://www.accellera.org/XMLSchema/IPXACT/1685-2014 http://www.accellera.org/XMLSchema/IPXACT/1685-2014/index.xsd">
	<ipxact:vendor>pulp-platform.org</ipxact:vendor>
	<ipxact:library>interface</ipxact:library>
	<ipxact:name>uart</ipxact:name>
	<ipxact:version>1.0</ipxact:version>
	<ipxact:busInterfaces>
		<ipxact:busInterface>
			<ipxact:name>rx</ipxact:name>
			<ipxact:busType vendor="pulp-platform.org" library="interface" name="uart_rx" version="1.0"/>
			<ipxact:abstractionTypes>
				<ipxact:abstractionType>
					<ipxact:abstractionRef vendor="pulp-platform.org" library="interface" name="uart_rx.absDef" version="1.0"/>
					<ipxact:portMaps>
						<ipxact:portMap>
							<ipxact:master>
								<ipxact:componentInstantiationRef>uart_rx_inst</ipxact:componentInstantiationRef>
								<ipxact:port>rx</ipxact:port>
							</ipxact:master>
							<ipxact:slave>
								<ipxact:vendor>pulp-platform.org</ipxact:vendor>
								<ipxact:library>communication.transceiver</ipxact:library>
								<ipxact:name>spi_transceiver</ipxact:name>
								<ipxact:version>1.0</ipxact:version>
								<ipxact:designRef>
									<ipxact:component vendor="pulp-platform.org" library="communication.transceiver" name="spi_transceiver" version="1.0"/>
									<ipxact:view>transceiver</ipxact:view>
								</ipxact:designRef>
								<ipxact:designRef>
									<ipxact:component vendor="pulp-platform.org" library="communication.transceiver" name="spi_transceiver" version="1.0"/>
									<ipxact:view>transmitter</ipxact:view>
								</ipxact:designRef>
							</ipxact:slave>
						</ipxact:portMap>
					</ipxact:portMaps>
				</ipxact:abstractionType>
			</ipxact:abstractionTypes>
		</ipxact:busInterface>
		<ipxact:busInterface>
			<ipxact:name>tx</ipxact:name>
			<ipxact:busType vendor="pulp-platform.org" library="interface" name="uart_tx" version="1.0"/>
			<ipxact:abstractionTypes>
				<ipxact:abstractionType>
					<ipxact:abstractionRef vendor="pulp-platform.org" library="interface" name="uart_tx.absDef" version="1.0"/>
					<ipxact:portMaps>
						<ipxact:portMap>
							<ipxact:master>
								<ipxact:componentInstantiationRef>uart_tx_inst</ipxact:componentInstantiationRef>
								<ipxact:port>tx</ipxact:port>
							</ipxact:master>
							<ipxact:slave>
								<ipxact:vendor>pulp-platform.org</ipxact:vendor>
								<ipxact:library>communication.transceiver</ipxact:library>
								<ipxact:name>spi_transceiver</ipxact:name>
								<ipxact:version>1.0</ipxact:version>
								<ipxact:designRef>
									<ipxact:component vendor="pulp-platform.org" library="communication.transceiver" name="spi_transceiver" version="1.0"/>
									<ipxact:view>transceiver</ipxact:view>
								</ipxact:designRef>
								<ipxact:designRef>
									<ipxact:component vendor="pulp-platform.org" library="communication.transceiver" name="spi_transceiver" version="1.0"/>
									<ipxact:view>receiver</ipxact:view>
								</ipxact:designRef>
							</ipxact:slave>
						</ipxact:portMap>
					</ipxact:portMaps>
				</ipxact:abstractionType>
			</ipxact:abstractionTypes>
		</ipxact:busInterface>
	</ipxact:busInterfaces>
	<ipxact:componentInstantiations>
		<ipxact:componentInstantiation>
			<ipxact:instanceName>uart_rx_inst</ipxact:instanceName>
			<ipxact:description>UART receiver</ipxact:description>
			<ipxact:componentRef vendor="pulp-platform.org" library="communication.transceiver" name="spi_transceiver" version="1.0"/>
			<ipxact:designs>
				<ipxact:design>
					<ipxact:designRef vendor="pulp-platform.org" library="communication.transceiver" name="spi_transceiver" version="1.0"/>
					<ipxact:view>transceiver</ipxact:view>
					<ipxact:designContents>
						<ipxact:vendor>pulp-platform.org</ipxact:vendor>
						<ipxact:library>communication.transceiver</ipxact:library>
						<ipxact:name>spi_transceiver</ipxact:name>
						<ipxact:version>1.0</ipxact:version>
						<ipxact:designElements>
							<ipxact:designElement>
								<ipxact:name>spi_transceiver_i</ipxact:name>"""
component_name = "ipxact_component"


API Key successfully retrieved.


In [81]:
import ipywidgets as widgets
from IPython.display import display
button = widgets.Button(description="Click to assess!")
output = widgets.Output()

def on_button_clicked(b):
  # Display the message within the output widget.
  with output:
    assess_and_save_xml(xml_data, component_name)
    print("Assesment completed!")

button.on_click(on_button_clicked)
display(button, output)

Button(description='Click to assess!', style=ButtonStyle())

Output()

In [63]:
eval_prompt_2 = "Generate an IP-XACT component for wishbone."
model_input_2 = tokenizer(eval_prompt_2, return_tensors="pt").to("cuda")
with torch.no_grad():
    output_2 = tokenizer.decode(model.generate(**model_input_2, max_new_tokens = 2048, pad_token_id=tokenizer.eos_token_id)[0], skip_special_tokens=True)

print(output_2)

Generate an IP-XACT component for wishbone. <?xml version="1.0" encoding="UTF-8"?>
<ipxact:busDefinition xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xmlns:ipxact="http://www.accellera.org/XMLSchema/IPXACT/1685-2014" xmlns:kactus2="http://kactus2.cs.tut.fi" xsi:schemaLocation="http://www.accellera.org/XMLSchema/IPXACT/1685-2014 http://www.accellera.org/XMLSchema/IPXACT/1685-2014/index.xsd">
	<ipxact:vendor>pulp-platform.org</ipxact:vendor>
	<ipxact:library>interface</ipxact:library>
	<ipxact:name>wishbone</ipxact:name>
	<ipxact:version>1.0</ipxact:version>
	<ipxact:directConnection>true</ipxact:directConnection>
	<ipxact:isAddressable>true</ipxact:isAddressable>
	<ipxact:isBidirectional>true</ipxact:isBidirectional>
	<ipxact:maxMasters>1</ipxact:maxMasters>
	<ipxact:maxSlaves>1</ipxact:maxSlaves>
	<ipxact:vendorExtensions>
		<kactus2:version>2,0,0,0</kactus2:version>
	</ipxact:vendorExtensions>
</ipxact:busDefinition>

